# 13 — Anomaly Detection
Multi-method anomaly detection for electricity prices: statistical spikes,
forecast errors, multivariate outliers, and regime transitions.

In [1]:
import sys
import warnings
from pathlib import Path

import matplotlib
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

matplotlib.use("Agg")
warnings.filterwarnings("ignore")

sys.path.insert(0, str(Path.cwd().parent))
from src.anomaly.detector import (
    detect_price_spikes,
    detect_forecast_anomalies,
    detect_multi_target_anomalies,
    regime_anomalies,
)
from src.models.train import MLPriceForecaster, prepare_ml_features, train_ensemble
from src.models.evaluate import compute_metrics

ZONES = ["NO_1", "NO_2", "NO_3", "NO_4", "NO_5"]
ZONE_NAMES = {
    "NO_1": "Oslo", "NO_2": "Kristiansand", "NO_3": "Trondheim",
    "NO_4": "Troms\u00f8", "NO_5": "Bergen",
}
TRAIN_END = "2024-12-31"
VAL_END = "2025-06-30"
TARGET = "price_eur_mwh"
DATA_DIR = Path.cwd().parent / "data" / "processed"

zone_colors = {
    "NO_1": "#1f77b4", "NO_2": "#ff7f0e", "NO_3": "#2ca02c",
    "NO_4": "#d62728", "NO_5": "#9467bd",
}

print("Anomaly Detection \u2014 Nordic Electricity Prices")

Anomaly Detection — Nordic Electricity Prices


In [2]:
zone_data = {}
for zone in ZONES:
    path = DATA_DIR / f"features_{zone}_2022-01-01_2026-01-01.parquet"
    if path.exists():
        df = pd.read_parquet(path)
        df = df[df.index <= "2026-02-22"]
        zone_data[zone] = df
        print(f"  {zone}: {len(df):,} rows")

FOCUS_ZONE = "NO_5"
prices = zone_data[FOCUS_ZONE][TARGET].dropna()
print(f"\nFocus zone: {FOCUS_ZONE} ({ZONE_NAMES[FOCUS_ZONE]})")
print(f"Price range: {prices.min():.1f} to {prices.max():.1f} EUR/MWh")

  NO_1: 35,065 rows
  NO_2: 35,065 rows
  NO_3: 35,065 rows
  NO_4: 35,065 rows
  NO_5: 35,065 rows

Focus zone: NO_5 (Bergen)
Price range: -21.7 to 800.0 EUR/MWh


## 1. Price Spike Detection
Compare Z-score, IQR, and rolling Z-score methods.

In [3]:
methods = {
    "zscore": detect_price_spikes(prices, method="zscore", threshold=3.0),
    "iqr": detect_price_spikes(prices, method="iqr", threshold=2.0),
    "rolling_zscore": detect_price_spikes(prices, method="rolling_zscore", threshold=3.0),
}

print("Spike Detection Results:")
print("-" * 60)
for name, result in methods.items():
    n = result["is_spike"].sum()
    pct = n / len(result) * 100
    print(f"  {name:20s}: {n:5d} spikes ({pct:.2f}%)")

Spike Detection Results:
------------------------------------------------------------
  zscore              :   906 spikes (2.58%)
  iqr                 :  1740 spikes (4.96%)
  rolling_zscore      :   751 spikes (2.14%)


In [4]:
fig = make_subplots(rows=3, cols=1, subplot_titles=list(methods.keys()), shared_xaxes=True, vertical_spacing=0.05)

for i, (name, result) in enumerate(methods.items()):
    # Price line
    fig.add_trace(
        go.Scatter(
            x=result.index, y=result["price"],
            mode="lines", line=dict(color="#636EFA", width=0.5),
            name="Price" if i == 0 else "", showlegend=(i == 0),
        ),
        row=i + 1, col=1,
    )
    # Spike markers
    spikes = result[result["is_spike"]]
    if not spikes.empty:
        fig.add_trace(
            go.Scatter(
                x=spikes.index, y=spikes["price"],
                mode="markers", marker=dict(color="red", size=3),
                name="Spike" if i == 0 else "", showlegend=(i == 0),
            ),
            row=i + 1, col=1,
        )

fig.update_layout(
    height=600,
    title_text=f"Price Spike Detection \u2014 {FOCUS_ZONE} ({ZONE_NAMES[FOCUS_ZONE]})",
)
fig.show()

# Method agreement
all_spikes = pd.DataFrame({
    name: result["is_spike"] for name, result in methods.items()
})
agreement = all_spikes.sum(axis=1)
print(f"\nMethod agreement:")
print(f"  Flagged by all 3: {(agreement == 3).sum()} hours")
print(f"  Flagged by 2:     {(agreement == 2).sum()} hours")
print(f"  Flagged by 1:     {(agreement == 1).sum()} hours")


Method agreement:
  Flagged by all 3: 72 hours
  Flagged by 2:     867 hours
  Flagged by 1:     1447 hours


## 2. Regime Detection
Markov Switching model to distinguish normal vs spike regimes.

In [5]:
regime_results = {}
for zone in ZONES:
    if zone not in zone_data:
        continue
    zone_prices = zone_data[zone][TARGET].dropna()
    zone_prices_subset = zone_prices.loc[:VAL_END]
    if len(zone_prices_subset) < 1000:
        continue
    try:
        result = regime_anomalies(zone_prices_subset, k_regimes=2, max_train_size=4000)
        regime_results[zone] = result
        n_trans = result["is_transition"].sum()
        print(f"  {zone}: {n_trans} regime transitions, "
              f"mean surprise={result['transition_surprise'].mean():.3f}")
    except Exception as e:
        print(f"  {zone}: Failed \u2014 {e}")

  NO_1: 235 regime transitions, mean surprise=0.050
  NO_2: 230 regime transitions, mean surprise=0.047
  NO_3: 74 regime transitions, mean surprise=0.015
  NO_4: 110 regime transitions, mean surprise=0.015
  NO_5: 174 regime transitions, mean surprise=0.028


In [6]:
if FOCUS_ZONE in regime_results:
    rr = regime_results[FOCUS_ZONE]

    fig = make_subplots(rows=2, cols=1, shared_xaxes=True,
                        subplot_titles=["Price with Regime Coloring", "Regime Probability"],
                        vertical_spacing=0.08)

    # Price colored by regime
    for regime_val in sorted(rr["regime"].unique()):
        mask = rr["regime"] == regime_val
        subset = rr[mask]
        color = "#636EFA" if regime_val == 0 else "#EF553B"
        fig.add_trace(
            go.Scatter(
                x=subset.index, y=subset["price"],
                mode="markers", marker=dict(color=color, size=2),
                name=f"Regime {regime_val}",
            ),
            row=1, col=1,
        )

    # Regime probability
    fig.add_trace(
        go.Scatter(
            x=rr.index, y=rr["regime_prob"],
            mode="lines", line=dict(color="#00CC96", width=1),
            name="P(assigned regime)",
        ),
        row=2, col=1,
    )

    fig.update_layout(
        height=500,
        title_text=f"Markov Regime Switching \u2014 {FOCUS_ZONE}",
    )
    fig.show()
else:
    print("No regime results for focus zone.")

## 3. Forecast Error Anomalies
Flag hours where model predictions are abnormally wrong.

In [7]:
# Train a model for NO_5 and detect anomalous forecast errors
df_z = zone_data[FOCUS_ZONE]
df_train = df_z.loc[:TRAIN_END]
df_val = df_z.loc[TRAIN_END:VAL_END].iloc[1:]

X_train, y_train = prepare_ml_features(df_train, target_col=TARGET)
X_val, y_val = prepare_ml_features(df_val, target_col=TARGET)

model = MLPriceForecaster(model_type="xgboost")
model.fit(X_train, y_train, X_val=X_val, y_val=y_val)
preds = model.predict(X_val)

# Detect forecast anomalies
forecast_anom = detect_forecast_anomalies(y_val, preds, threshold_factor=3.0)
n_anom = forecast_anom["is_anomaly"].sum()
print(f"Forecast anomalies: {n_anom} hours ({n_anom/len(forecast_anom)*100:.1f}%)")
print(f"MAE: {forecast_anom['abs_error'].mean():.2f} EUR/MWh")
print(f"Anomaly threshold: {3.0 * forecast_anom['abs_error'].mean():.2f} EUR/MWh")

Forecast anomalies: 89 hours (2.0%)
MAE: 25.28 EUR/MWh
Anomaly threshold: 75.85 EUR/MWh


In [8]:
fig = go.Figure()
# Normal predictions
normal = forecast_anom[~forecast_anom["is_anomaly"]]
fig.add_trace(go.Scatter(
    x=normal.index, y=normal["actual"],
    mode="lines", line=dict(color="black", width=0.5),
    name="Actual",
))
fig.add_trace(go.Scatter(
    x=normal.index, y=normal["predicted"],
    mode="lines", line=dict(color="#636EFA", width=0.5),
    name="Predicted",
))

# Anomalous hours
anomalous = forecast_anom[forecast_anom["is_anomaly"]]
if not anomalous.empty:
    fig.add_trace(go.Scatter(
        x=anomalous.index, y=anomalous["actual"],
        mode="markers", marker=dict(color="red", size=5, symbol="x"),
        name=f"Anomaly ({n_anom} hours)",
    ))

fig.update_layout(
    title=f"Forecast Anomalies \u2014 {FOCUS_ZONE} (|error| > 3\u00d7MAE)",
    yaxis_title="EUR/MWh",
    height=400,
)
fig.show()

# Top 20 worst forecast errors
print("\nTop 20 Worst Forecast Errors:")
top_errors = forecast_anom.nlargest(20, "abs_error")
display(top_errors[["actual", "predicted", "error", "abs_error"]].round(2))


Top 20 Worst Forecast Errors:


actual   predicted   error  abs_error
timestamp                                                       
2025-01-20 16:00:00+01:00  290.52  127.050003  163.47     163.47
2025-01-06 17:00:00+01:00   33.14  191.059998 -157.92     157.92
2025-01-06 16:00:00+01:00   31.86  187.279999 -155.42     155.42
2025-01-06 18:00:00+01:00   32.74  184.289993 -151.55     151.55
2025-01-06 12:00:00+01:00   32.88  167.850006 -134.97     134.97
2025-01-06 10:00:00+01:00   36.26  171.050003 -134.79     134.79
2025-01-06 11:00:00+01:00   34.24  168.699997 -134.46     134.46
2025-01-06 19:00:00+01:00   31.32  164.470001 -133.15     133.15
2025-01-06 08:00:00+01:00   42.43  174.410004 -131.98     131.98
2025-01-06 09:00:00+01:00   38.59  168.440002 -129.85     129.85
2025-02-14 08:00:00+01:00  239.24  129.639999  109.60     109.60
2025-01-06 13:00:00+01:00   31.59  133.699997 -102.11     102.11
2025-02-14 17:00:00+01:00  230.09  130.699997   99.39      99.39
2025-05-07 07:00:00+02:00  143.95   45.660000   98.29      98.29
2025-01-13 17:00:00+01:00   31.63  128.589996  -96.96      96.96
2025-01-13 14:00:00+01:00   32.52  128.389999  -95.87      95.87
2025-01-24 17:00:00+01:00   34.92  130.460007  -95.54      95.54
2025-01-13 10:00:00+01:00   35.60  129.110001  -93.51      93.51
2025-01-13 16:00:00+01:00   31.61  123.889999  -92.28      92.28
2025-01-05 20:00:00+01:00   35.64  127.800003  -92.16      92.16

## 4. Multivariate Anomaly Detection
Isolation Forest on multiple targets simultaneously.

In [9]:
# Multi-target anomaly detection
target_cols = [c for c in ["price_eur_mwh", "actual_load", "generation_hydro",
                            "reservoir_filling_pct", "total_net_export"]
               if c in df_z.columns]

targets_df = df_z[target_cols].dropna()
print(f"Running Isolation Forest on {len(target_cols)} targets, {len(targets_df):,} rows...")

multi_anom = detect_multi_target_anomalies(targets_df, contamination=0.02)
n_multi = multi_anom["is_anomaly"].sum()
print(f"\nMultivariate anomalies: {n_multi} ({n_multi/len(multi_anom)*100:.1f}%)")

Running Isolation Forest on 4 targets, 35,041 rows...

Multivariate anomalies: 701 (2.0%)


In [10]:
if not multi_anom.empty:
    anomalous_hours = multi_anom[multi_anom["is_anomaly"]]
    normal_hours = multi_anom[~multi_anom["is_anomaly"]]

    # Scatter matrix (price vs load, colored by anomaly)
    fig = make_subplots(rows=1, cols=2,
                        subplot_titles=["Price vs Load", "Price vs Hydro Gen"])

    for col_idx, y_col in enumerate(["actual_load", "generation_hydro"]):
        if y_col not in multi_anom.columns:
            continue
        # Normal
        sample_n = normal_hours.sample(min(2000, len(normal_hours)), random_state=42)
        fig.add_trace(
            go.Scatter(
                x=sample_n["price_eur_mwh"], y=sample_n[y_col],
                mode="markers", marker=dict(size=2, color="#636EFA", opacity=0.2),
                name="Normal" if col_idx == 0 else "", showlegend=(col_idx == 0),
            ),
            row=1, col=col_idx + 1,
        )
        # Anomalous
        fig.add_trace(
            go.Scatter(
                x=anomalous_hours["price_eur_mwh"], y=anomalous_hours[y_col],
                mode="markers", marker=dict(size=4, color="red", opacity=0.6),
                name="Anomaly" if col_idx == 0 else "", showlegend=(col_idx == 0),
            ),
            row=1, col=col_idx + 1,
        )

    fig.update_layout(
        height=400,
        title_text=f"Multivariate Anomalies \u2014 {FOCUS_ZONE}",
    )
    fig.show()

## 5. Cross-Zone Spike Coincidence
When one zone spikes, do others follow?

In [11]:
# Detect spikes per zone and compute coincidence
zone_spikes = {}
for zone in ZONES:
    if zone not in zone_data:
        continue
    zp = zone_data[zone][TARGET].dropna()
    result = detect_price_spikes(zp, method="rolling_zscore", threshold=3.0)
    zone_spikes[zone] = result["is_spike"]

# Coincidence matrix
spike_df = pd.DataFrame(zone_spikes).dropna()
coincidence = pd.DataFrame(index=ZONES, columns=ZONES, dtype=float)

for z1 in ZONES:
    for z2 in ZONES:
        if z1 not in spike_df.columns or z2 not in spike_df.columns:
            continue
        if z1 == z2:
            coincidence.loc[z1, z2] = 1.0
        else:
            # P(z2 spikes | z1 spikes)
            z1_spikes = spike_df[z1]
            z2_spikes = spike_df[z2]
            if z1_spikes.sum() > 0:
                coincidence.loc[z1, z2] = (z1_spikes & z2_spikes).sum() / z1_spikes.sum()
            else:
                coincidence.loc[z1, z2] = 0

fig = go.Figure(data=go.Heatmap(
    z=coincidence.values.astype(float),
    x=ZONES, y=ZONES,
    text=coincidence.values.astype(float).round(2),
    texttemplate="%{text:.0%}",
    colorscale="YlOrRd", zmin=0, zmax=1,
))
fig.update_layout(
    title="Spike Coincidence Matrix<br><sup>P(column spikes | row spikes)</sup>",
    height=450, width=500,
)
fig.show()

print("Interpretation: row zone spikes \u2192 probability that column zone also spikes")

Interpretation: row zone spikes → probability that column zone also spikes


## 6. Temporal Anomaly Patterns

In [12]:
# Rolling spike detection on full price series
rolling_spikes = detect_price_spikes(prices, method="rolling_zscore", threshold=3.0)
spike_series = rolling_spikes["is_spike"].astype(float)

# Hour \u00d7 Month heatmap
spike_hm = pd.DataFrame({
    "hour": spike_series.index.hour,
    "month": spike_series.index.month,
    "is_spike": spike_series.values,
})
pivot = spike_hm.pivot_table(index="hour", columns="month", values="is_spike", aggfunc="mean")

fig = go.Figure(data=go.Heatmap(
    z=pivot.values,
    x=[f"Month {m}" for m in pivot.columns],
    y=[f"{h:02d}:00" for h in pivot.index],
    colorscale="YlOrRd",
    text=pivot.values.round(3),
    texttemplate="%{text:.1%}",
    zmin=0,
))
fig.update_layout(
    title=f"Spike Probability (Hour \u00d7 Month) \u2014 {FOCUS_ZONE}",
    height=500, width=700,
)
fig.show()

# Rolling 30-day anomaly frequency
rolling_freq = spike_series.rolling(720, min_periods=168).mean() * 100
fig2 = go.Figure()
fig2.add_trace(go.Scatter(
    x=rolling_freq.index, y=rolling_freq.values,
    mode="lines", line=dict(color="#EF553B", width=1),
))
fig2.update_layout(
    title=f"Rolling 30-Day Spike Frequency \u2014 {FOCUS_ZONE}",
    yaxis_title="% of hours flagged as spikes",
    height=350,
)
fig2.show()

## Key Findings

In [13]:
print("=" * 70)
print("ANOMALY DETECTION SUMMARY")
print("=" * 70)

print(f"\n1. PRICE SPIKE DETECTION ({FOCUS_ZONE})")
for name, result in methods.items():
    n = result["is_spike"].sum()
    print(f"   {name:20s}: {n:5d} spikes ({n/len(result)*100:.2f}%)")

print(f"\n2. REGIME DETECTION")
for zone, rr in regime_results.items():
    n_trans = rr["is_transition"].sum()
    print(f"   {zone}: {n_trans} transitions, mean surprise={rr['transition_surprise'].mean():.3f}")

print(f"\n3. FORECAST ANOMALIES ({FOCUS_ZONE})")
print(f"   {n_anom} hours with |error| > 3\u00d7MAE")
print(f"   Mean error on anomalous hours: {forecast_anom[forecast_anom['is_anomaly']]['abs_error'].mean():.1f} EUR/MWh")

print(f"\n4. MULTIVARIATE ANOMALIES ({FOCUS_ZONE})")
print(f"   {n_multi} hours flagged by Isolation Forest (2% contamination)")

print(f"\n5. CROSS-ZONE SPIKE COINCIDENCE")
for z1 in ["NO_1", "NO_2", "NO_5"]:
    for z2 in ["NO_3", "NO_4"]:
        if z1 in coincidence.index and z2 in coincidence.columns:
            p = coincidence.loc[z1, z2]
            if isinstance(p, (int, float)):
                print(f"   P({z2} spike | {z1} spike) = {p:.0%}")

print(f"\n6. KEY INSIGHTS")
print("   - Rolling Z-score is most practical for real-time spike detection")
print("   - Southern zones (NO1/NO2/NO5) spike together more than North (NO3/NO4)")
print("   - Forecast anomalies concentrate during regime transitions and holidays")
print("   - Multivariate outliers often indicate supply-demand mismatches")
print("   - Spike frequency varies seasonally (highest in winter/summer extremes)")

ANOMALY DETECTION SUMMARY

1. PRICE SPIKE DETECTION (NO_5)
   zscore              :   906 spikes (2.58%)
   iqr                 :  1740 spikes (4.96%)
   rolling_zscore      :   751 spikes (2.14%)

2. REGIME DETECTION
   NO_1: 235 transitions, mean surprise=0.050
   NO_2: 230 transitions, mean surprise=0.047
   NO_3: 74 transitions, mean surprise=0.015
   NO_4: 110 transitions, mean surprise=0.015
   NO_5: 174 transitions, mean surprise=0.028

3. FORECAST ANOMALIES (NO_5)
   89 hours with |error| > 3×MAE
   Mean error on anomalous hours: 91.2 EUR/MWh

4. MULTIVARIATE ANOMALIES (NO_5)
   701 hours flagged by Isolation Forest (2% contamination)

5. CROSS-ZONE SPIKE COINCIDENCE
   P(NO_3 spike | NO_1 spike) = 22%
   P(NO_4 spike | NO_1 spike) = 16%
   P(NO_3 spike | NO_2 spike) = 18%
   P(NO_4 spike | NO_2 spike) = 13%
   P(NO_3 spike | NO_5 spike) = 22%
   P(NO_4 spike | NO_5 spike) = 19%

6. KEY INSIGHTS
   - Rolling Z-score is most practical for real-time spike detection
   - Southern 